# Music Genre Prediction

In [24]:
class Config:
    NB = '001'
    dataset_NB = '101'
    emsemble_NB = ['nb301', 'nb302', 'nb303']

    raw_data_dir = '../data/raw/'
    processed_data_dir = '../data/processed/'
    interim_dir = '../data/interim/'
    submission_dir = '../data/submission/'

    random_seed = 42
    n_folds = 5

    row_id = 'index'
    target = 'genre'

## Import libralies

In [2]:
import gc
import warnings
warnings.filterwarnings('ignore')

import scipy as sp
import numpy as np
import pandas as pd
pd.set_option('display.max_rows', 500)
pd.set_option('display.max_columns', 500)
pd.set_option('display.width', 1000)
from tqdm.auto import tqdm
import itertools

import matplotlib.pyplot as plt
import seaborn as sns

%matplotlib inline
sns.set(style='white', context='notebook', palette='deep')

In [3]:
import plotly.graph_objects as go
from plotly.subplots import make_subplots

plotly_template = dict(
    layout=go.Layout(
        template='plotly_dark',
        font=dict(
            family="Franklin Gothic",
            size=12
        ),
        height=500,
        width=1000,
    )
)

color_palette = {
    'Bin': ['#016CC9','#E876A3'],
    'Cat5': ['#E876A3', '#E0A224', '#63B70D', '#6BCFF6', '#13399E'],
    'Cat10': ['#E876A3', '#E0A224', '#63B70D', '#6BCFF6', '#13399E', '#E876A3', '#E0A224', '#63B70D', '#6BCFF6', '#13399E'],
}

## Load data
- data数
  - train: 4046x14
  - test: 4046x13
- columns
  - targetは「genre」で、int
  - tempo　と　region がobjectな模様
- 欠損
  - train
    - positiveness: 10
    - danceability: 8
    - liveness: 3
    - speechiness: 8
    - instrumentalness: 1
    - region: 370(unknownという名称で入っている)
  - test
    - acousticness: 1
    - positiveness: 14
    - danceability: 11
    - energy: 1
    - liveness: 6
    - speechiness: 11
    - instrumentalness: 2
    - region: 320(unknownという名称で入っている)

### Insight:
- 欠損はtrainにもtestにも存在する。およそ均等に存在する。
- regionでunknownになっている数が最も多い。
  - 欠損と捉えて補完するのか、このまま扱うかを検討する必要がありそう。

In [4]:
df_train = pd.read_csv(Config.raw_data_dir + 'train.csv')
df_test = pd.read_csv(Config.raw_data_dir + 'test.csv')

In [7]:
df_train.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 4046 entries, 0 to 4045
Data columns (total 14 columns):
 #   Column            Non-Null Count  Dtype  
---  ------            --------------  -----  
 0   index             4046 non-null   int64  
 1   genre             4046 non-null   int64  
 2   popularity        4046 non-null   int64  
 3   duration_ms       4046 non-null   int64  
 4   acousticness      4046 non-null   float64
 5   positiveness      4036 non-null   float64
 6   danceability      4038 non-null   float64
 7   loudness          4046 non-null   float64
 8   energy            4046 non-null   float64
 9   liveness          4043 non-null   float64
 10  speechiness       4038 non-null   float64
 11  instrumentalness  4045 non-null   float64
 12  tempo             4046 non-null   object 
 13  region            4046 non-null   object 
dtypes: float64(8), int64(4), object(2)
memory usage: 442.7+ KB


In [8]:
df_test.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 4046 entries, 0 to 4045
Data columns (total 13 columns):
 #   Column            Non-Null Count  Dtype  
---  ------            --------------  -----  
 0   index             4046 non-null   int64  
 1   popularity        4046 non-null   int64  
 2   duration_ms       4046 non-null   int64  
 3   acousticness      4045 non-null   float64
 4   positiveness      4032 non-null   float64
 5   danceability      4035 non-null   float64
 6   loudness          4046 non-null   float64
 7   energy            4045 non-null   float64
 8   liveness          4040 non-null   float64
 9   speechiness       4035 non-null   float64
 10  instrumentalness  4044 non-null   float64
 11  tempo             4046 non-null   object 
 12  region            4046 non-null   object 
dtypes: float64(8), int64(3), object(2)
memory usage: 411.0+ KB


In [11]:
display(len(df_train[df_train['region'] == 'unknown']))
display(len(df_test[df_test['region'] == 'unknown']))

370

326

In [13]:
df_train.describe()

index        genre   popularity   duration_ms  acousticness  positiveness  danceability     loudness       energy     liveness  speechiness  instrumentalness
count  4046.000000  4046.000000  4046.000000  4.046000e+03   4046.000000   4036.000000   4038.000000  4046.000000  4046.000000  4043.000000  4038.000000       4045.000000
mean   2022.500000     7.281760    41.056105  2.421410e+05      0.346455      0.464100      0.504347    -7.715659     0.603663     0.265986     0.198655          0.214336
std    1168.123923     2.887542    16.165708  8.520241e+04      0.241004      0.225052      0.158415     4.109640     0.201020     0.155769     0.083557          0.154281
min       0.000000     0.000000     0.000000  5.998000e+03      0.000000      0.000000      0.013839   -37.820457     0.003383     0.000000     0.000000          0.000000
25%    1011.250000     7.000000    31.000000  2.044420e+05      0.149705      0.276384      0.392581    -9.775363     0.462137     0.168527     0.148698          0.143295
50%    2022.500000     8.000000    42.000000  2.358735e+05      0.250711      0.450211      0.510993    -7.189460     0.634078     0.218486     0.183190          0.171708
75%    3033.750000    10.000000    52.000000  2.724020e+05      0.523088      0.644786      0.617371    -4.876553     0.768768     0.317773     0.224999          0.205446
max    4045.000000    10.000000    82.000000  2.135773e+06      1.000000      0.989661      1.000000     0.000000     1.000000     1.000000     0.886806          1.000000

In [14]:
df_train

index  genre  popularity  duration_ms  acousticness  positiveness  danceability   loudness    energy  liveness  speechiness  instrumentalness    tempo    region
0         0     10          11       201094      0.112811      0.157247      0.187841  -1.884852  0.893918  0.363568     0.390108          0.888884  121-152  region_H
1         1      8          69       308493      0.101333      0.346563      0.554444  -5.546495  0.874409  0.193892     0.161497          0.123910  153-176  region_I
2         2      3          43       197225      0.496420      0.265391      0.457642  -9.255670  0.439933  0.217146     0.369057          0.166470    64-76  region_E
3         3     10          45       301092      0.165667      0.245533      0.356578  -5.088788  0.868704  0.377025     0.226677          0.175399  177-192  region_C
4         4      3          57       277348      0.190720      0.777578      0.830479  -3.933896  0.650149  0.169323     0.222488          0.226030   97-120   unknown
...     ...    ...         ...          ...           ...           ...           ...        ...       ...       ...          ...               ...      ...       ...
4041   4041     10          38       246309      0.128795      0.329718      0.575830  -5.252543  0.509531  0.193781     0.187331          0.158197  121-152  region_P
4042   4042      5          23       208734      0.778732      0.228757      0.394283 -14.225700  0.322871  0.253108     0.141218          0.295608  121-152  region_D
4043   4043     10          30       407016      0.402050      0.462374      0.672265 -10.711253  0.646571  0.228189     0.152270          0.163483   97-120  region_E
4044   4044     10          25       204957      0.208096      0.465511      0.523514  -7.855946  0.508910  0.247820     0.202238          0.210184    77-96  region_R
4045   4045      3          38       185527      0.213589      0.945140      0.732470  -5.035310  0.736477  0.206115     0.424272          0.158386   97-120  region_E

[4046 rows x 14 columns]

### 文字列カテゴリの確認
- tempoに含まれる文字列の種類はtrainとtestで同じ
- regionに含まれる文字列の種類は、region_Mがtrainのみに存在し、testには無い

In [20]:
display(sorted(df_train['tempo'].unique()))
display(sorted(df_test['tempo'].unique()))

['0-40',
 '121-152',
 '153-176',
 '177-192',
 '193-208',
 '209-220',
 '41-50',
 '51-56',
 '57-63',
 '64-76',
 '77-96',
 '97-120']

['0-40',
 '121-152',
 '153-176',
 '177-192',
 '193-208',
 '209-220',
 '41-50',
 '51-56',
 '57-63',
 '64-76',
 '77-96',
 '97-120']

In [21]:
display(sorted(df_train['region'].unique()))
display(sorted(df_test['region'].unique()))

['region_A',
 'region_B',
 'region_C',
 'region_D',
 'region_E',
 'region_F',
 'region_G',
 'region_H',
 'region_I',
 'region_J',
 'region_K',
 'region_L',
 'region_M',
 'region_N',
 'region_O',
 'region_P',
 'region_Q',
 'region_R',
 'region_S',
 'region_T',
 'unknown']

['region_A',
 'region_B',
 'region_C',
 'region_D',
 'region_E',
 'region_F',
 'region_G',
 'region_H',
 'region_I',
 'region_J',
 'region_K',
 'region_L',
 'region_N',
 'region_O',
 'region_P',
 'region_Q',
 'region_R',
 'region_S',
 'region_T',
 'unknown']

In [83]:
df_train

index  genre  popularity  duration_ms  acousticness  positiveness  danceability   loudness    energy  liveness  speechiness  instrumentalness    tempo    region
0         0     10          11       201094      0.112811      0.157247      0.187841  -1.884852  0.893918  0.363568     0.390108          0.888884  121-152  region_H
1         1      8          69       308493      0.101333      0.346563      0.554444  -5.546495  0.874409  0.193892     0.161497          0.123910  153-176  region_I
2         2      3          43       197225      0.496420      0.265391      0.457642  -9.255670  0.439933  0.217146     0.369057          0.166470    64-76  region_E
3         3     10          45       301092      0.165667      0.245533      0.356578  -5.088788  0.868704  0.377025     0.226677          0.175399  177-192  region_C
4         4      3          57       277348      0.190720      0.777578      0.830479  -3.933896  0.650149  0.169323     0.222488          0.226030   97-120   unknown
...     ...    ...         ...          ...           ...           ...           ...        ...       ...       ...          ...               ...      ...       ...
4041   4041     10          38       246309      0.128795      0.329718      0.575830  -5.252543  0.509531  0.193781     0.187331          0.158197  121-152  region_P
4042   4042      5          23       208734      0.778732      0.228757      0.394283 -14.225700  0.322871  0.253108     0.141218          0.295608  121-152  region_D
4043   4043     10          30       407016      0.402050      0.462374      0.672265 -10.711253  0.646571  0.228189     0.152270          0.163483   97-120  region_E
4044   4044     10          25       204957      0.208096      0.465511      0.523514  -7.855946  0.508910  0.247820     0.202238          0.210184    77-96  region_R
4045   4045      3          38       185527      0.213589      0.945140      0.732470  -5.035310  0.736477  0.206115     0.424272          0.158386   97-120  region_E

[4046 rows x 14 columns]

In [89]:
region_list = sorted(df_train['region'].unique())

fig = make_subplots(
    rows=4,
    cols=6,
    #start_cell='bottom-left', # どのセルを起点とするか
    subplot_titles=region_list,
    shared_xaxes=True, # x軸を共有する場合
    shared_yaxes=False, # y軸を共有する場合
)
for idx, region in enumerate(region_list):
    fig.add_trace(
    go.Histogram(
        x=df_train[df_train['region'] == region][Config.target],
        name=f'Target',
        #histnorm='probability',
        marker=dict(color=color_palette['Bin'][0]),
        #line=dict(color='black')
    ),
    row=int(idx/6) + 1,
    col=idx%6 + 1

)

fig.update_layout(
    title='Target Distribution',
    uniformtext_minsize=15,
    uniformtext_mode='hide',
    height=1500,
)

fig.show()

In [94]:
target_list = [i for i in range(11)]

fig = make_subplots(
    rows=3,
    cols=4,
    #start_cell='bottom-left', # どのセルを起点とするか
    subplot_titles=target_list,
    shared_xaxes=True, # x軸を共有する場合
    shared_yaxes=False, # y軸を共有する場合
)

for idx, i in enumerate(target_list):
    fig.add_trace(
    go.Histogram(
        x=df_train[df_train[Config.target] == i]['region'],
        name=f'Target',
        #histnorm='probability',
        marker=dict(color=color_palette['Bin'][0]),
        #line=dict(color='black')
    ),
    row=int(idx/4) + 1,
    col=idx%4 + 1

)

fig.update_layout(
    title='Target Distribution',
    uniformtext_minsize=15,
    uniformtext_mode='hide',
    height=1500,
)

fig.show()

### 数値カテゴリの確認
- trainとtestでほとんど分布は変わらなさそう
- popularityで、80くらいにひとつの山がある？

In [22]:
col_list = [col for col in df_test.columns if df_test[col].dtype != object]

fig = make_subplots(
    rows=3,
    cols=4,
    #start_cell='bottom-left', # どのセルを起点とするか
    subplot_titles=col_list,
    shared_xaxes=False, # x軸を共有する場合
    shared_yaxes=False, # y軸を共有する場合
)

for idx, col in enumerate(col_list):
    fig.add_trace(
        go.Histogram(
            x=df_train[col],
            name=f'{col}(Train)',
            histnorm='probability',
            marker=dict(color=color_palette['Bin'][0]),
            #line=dict(color='black')
        ),
        row=int(idx/4) + 1,
        col=idx%4 + 1
    )
    fig.add_trace(
        go.Histogram(
            x=df_test[col],
            name=f'{col}(Test)',
            histnorm='probability',
            marker=dict(color=color_palette['Bin'][1]),
            opacity=0.5
            #line=dict(color='black')
        ),
        row=int(idx/4) + 1,
        col=idx%4 + 1
    )


fig.update_layout(
    barmode='overlay',
    width=1500,
    height=1500,
)
fig.show()

## Targetの分布
- 8, 10に大きく偏っている
- 0, 4, 6, 9が非常に少ないので、どう予測させるかが重要な気がする

In [30]:
df_target_num = df_train[Config.target].value_counts().sort_index(ascending=False)

fig = go.Figure(layout=plotly_template['layout'])

fig.add_trace(
    go.Pie(
        labels=df_target_num.index,
        values=df_target_num,
        #hole=.45,
        showlegend=True,
        sort=False,
        marker=dict(
            colors=color_palette['Cat10'],
            line=dict(color=color_palette['Cat10'], width=2.5)
        ),
        hovertemplate="%{label} Genre: %{value:.2f}",
    )
)

fig.update_layout(
    title='Target Distribution',
    legend=dict(traceorder='reversed', y=1.05, x=0),
    uniformtext_minsize=15,
    uniformtext_mode='hide',
    width=700)

fig.show()

In [32]:
fig = go.Figure(layout=plotly_template['layout'])
fig.add_trace(
    go.Histogram(
        x=df_train[Config.target],
        name=f'Target',
        #histnorm='probability',
        marker=dict(color=color_palette['Bin'][0]),
        #line=dict(color='black')
    ),
)

fig.update_layout(
    title='Target Distribution',
    uniformtext_minsize=15,
    uniformtext_mode='hide',
    width=700)

fig.show()

## Targetと各変数の分布
- popularity
  - Target_0,9 の平均値が高い
  - Target_5が若干低い
- duration_ms
  - Target_10にのみめっちゃ長い曲がありそう。
    - 一定の長さ以上であるかという特徴量を加えることで、Target_10を特定するのに役立ちそう
- acousticness
  - 高めのTargetと低めのターゲットで分かれているような気がする
  - Target_4,6は平均値が高い
- energy
  - Target_4,6,7が若干低いかな
- speechiness
  - Target_3の平均値が高い
- instrumentalness
  - Target_6の分布が他と異なっている
    - 平均値も高い
  - Target_10も高い値を取りやすいようだが、Target_6の分類には十分寄与しそう

In [76]:
df_train.groupby(Config.target).describe()

index                                                                   popularity                                                       duration_ms                                                                                    acousticness                                                                       positiveness                                                                       danceability                                                                       loudness                                                                            energy                                                                       liveness                                                                       speechiness                                                                       instrumentalness                                                                      
        count         mean          std   min      25%     50%      75%     max      count       mean        std   min    25%   50%    75%   max       count           mean            std       min        25%       50%        75%        max        count      mean       std       min       25%       50%       75%       max        count      mean       std       min       25%       50%       75%       max        count      mean       std       min       25%       50%       75%       max    count       mean       std        min        25%        50%       75%       max   count      mean       std       min       25%       50%       75%       max    count      mean       std       min       25%       50%       75%       max       count      mean       std       min       25%       50%       75%       max            count      mean       std       min       25%       50%       75%       max
genre                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                            
0        32.0  1965.937500  1335.689092  20.0   794.25  1836.0  3406.75  4026.0       32.0  62.375000  16.676717  11.0  65.00  67.0  68.25  82.0        32.0  228303.562500   28240.296733  183305.0  204670.75  224816.0  255958.25   274545.0         32.0  0.278668  0.169594  0.047048  0.175372  0.223835  0.367339  0.698777         32.0  0.559857  0.202935  0.147544  0.386968  0.619958  0.723526  0.940727         32.0  0.556328  0.117867  0.336912  0.453350  0.564099  0.638108  0.790989     32.0  -6.283481  2.995615 -13.970634  -7.851498  -6.596818 -4.043205 -0.769015    32.0  0.616083  0.161809  0.341714  0.470487  0.644423  0.763875  0.840018     32.0  0.224763  0.110404  0.061512  0.144804  0.200602  0.315316  0.465508        32.0  0.182526  0.049571  0.066649  0.137741  0.184146  0.225202  0.288472             32.0  0.165733  0.035955  0.108785  0.141346  0.166347  0.185930  0.253305
1       205.0  2132.951220  1213.947021  24.0  1044.00  2173.0  3227.00  4020.0      205.0  41.039024  15.316544   6.0  28.00  42.0  53.00  72.0       205.0  248802.326829   73429.664850   37491.0  210014.00  238734.0  272598.00   635217.0        205.0  0.251741  0.194464  0.023088  0.126788  0.175807  0.309016  0.929160        205.0  0.484411  0.238180  0.000000  0.277062  0.479517  0.683069  0.941498        205

In [75]:
col_list = [col for col in df_test.columns if col not in [Config.row_id, Config.target]]

fig = make_subplots(
    rows=12,
    cols=1,
    #start_cell='bottom-left', # どのセルを起点とするか
    subplot_titles=col_list,
    shared_xaxes=False, # x軸を共有する場合
    shared_yaxes=True, # y軸を共有する場合
)

for idx, col in enumerate(col_list):
    for genre in range(11):
        fig.add_trace(
            go.Box(
                y=df_train[df_train[Config.target] == genre][col],
                name=f'Target_{genre}',
                marker=dict(color=color_palette['Bin'][0]),
                #line=dict(color='black')
            ),
            row=idx + 1,
            col=1,
        )

    fig.update_layout(
        title='Distribution',
        showlegend=False,
        barmode='overlay',
        width=1500,
        height=2500,
    )

fig.show()

In [66]:
col_list = [col for col in df_test.columns if col not in [Config.row_id, Config.target]]

for idx, col in enumerate(col_list):

    fig = make_subplots(
        rows=3,
        cols=4,
        #start_cell='bottom-left', # どのセルを起点とするか
        subplot_titles=[f'Target {i}' for i in range(11)],
        shared_xaxes=True, # x軸を共有する場合
        shared_yaxes=True, # y軸を共有する場合
    )

    for genre in range(11):
        fig.add_trace(
            go.Histogram(
                x=df_train[df_train[Config.target] == genre][col],
                #name=f'{col}(Train)',
                histnorm='probability',
                marker=dict(color=color_palette['Bin'][0]),
                #line=dict(color='black')
            ),
            row=int(genre/4) + 1,
            col=genre%4 + 1,
        )

    fig.update_layout(
        title=f'{col}',
        barmode='overlay',
        width=1500,
        height=1500,
    )
    fig.show()

In [63]:
# 相関行列を生成
from sklearn.preprocessing import OneHotEncoder

df_train_tmp = df_train.copy()

col_list = [Config.target]
output_col_list = [f'Target_{i}' for i in range(11)]

ohe = OneHotEncoder(sparse=False)
ohe.fit(df_train_tmp[col_list])

df_train_tmp[output_col_list] = ohe.transform(df_train_tmp[col_list])
df_train_tmp.drop(columns=col_list, inplace=True)

for i in range(11):
    col_list = [col for col in df_test.columns if col not in [Config.row_id]]
    col_list.append(f'Target_{i}')

    df_corr = df_train_tmp[col_list].corr()

    fig = go.Figure(layout=plotly_template['layout'])

    fig.add_trace(
        go.Heatmap(
            x=df_corr.columns,
            y=df_corr.index,
            z=np.array(df_corr),
            #annotation_text=np.around(np.array(df_corr), decimals=2),
            #y=total,
            name='Corr',
            colorscale='oxy'
            #mode='markers',
            #marker=dict(size=1, color='red'),
            #line=dict(color='black'),
            #customdata=total,
            #hovertemplate="<b>%{y:.2f}</b> <br>total: %{customdata:.2f}<extra></extra>",
        ),
    )

    fig.update_layout(
        width=1500,
        height=500,
    )

    fig.show()

index   popularity   duration_ms  acousticness  positiveness  danceability     loudness       energy     liveness  speechiness  instrumentalness     Target_0     Target_1     Target_2     Target_3     Target_4     Target_5     Target_6     Target_7     Target_8     Target_9    Target_10
count  4046.000000  4046.000000  4.046000e+03   4046.000000   4036.000000   4038.000000  4046.000000  4046.000000  4043.000000  4038.000000       4045.000000  4046.000000  4046.000000  4046.000000  4046.000000  4046.000000  4046.000000  4046.000000  4046.000000  4046.000000  4046.000000  4046.000000
mean   2022.500000    41.056105  2.421410e+05      0.346455      0.464100      0.504347    -7.715659     0.603663     0.265986     0.198655          0.214336     0.007909     0.050667     0.047207     0.089471     0.011122     0.031142     0.012358     0.082551     0.322541     0.014582     0.330450
std    1168.123923    16.165708  8.520241e+04      0.241004      0.225052      0.158415     4.109640     0.201020     0.155769     0.083557          0.154281     0.088591     0.219345     0.212108     0.285458     0.104886     0.173723     0.110491     0.275236     0.467506     0.119888     0.470433
min       0.000000     0.000000  5.998000e+03      0.000000      0.000000      0.013839   -37.820457     0.003383     0.000000     0.000000          0.000000     0.000000     0.000000     0.000000     0.000000     0.000000     0.000000     0.000000     0.000000     0.000000     0.000000     0.000000
25%    1011.250000    31.000000  2.044420e+05      0.149705      0.276384      0.392581    -9.775363     0.462137     0.168527     0.148698          0.143295     0.000000     0.000000     0.000000     0.000000     0.000000     0.000000     0.000000     0.000000     0.000000     0.000000     0.000000
50%    2022.500000    42.000000  2.358735e+05      0.250711      0.450211      0.510993    -7.189460     0.634078     0.218486     0.183190          0.171708     0.000000     0.000000     0.000000     0.000000     0.000000     0.000000     0.000000     0.000000     0.000000     0.000000     0.000000
75%    3033.750000    52.000000  2.724020e+05      0.523088      0.644786      0.617371    -4.876553     0.768768     0.317773     0.224999          0.205446     0.000000     0.000000     0.000000     0.000000     0.000000     0.000000     0.000000     0.000000     1.000000     0.000000     1.000000
max    4045.000000    82.000000  2.135773e+06      1.000000      0.989661      1.000000     0.000000     1.000000     1.000000     0.886806          1.000000     1.000000     1.000000     1.000000     1.000000     1.000000     1.000000     1.000000     1.000000     1.000000     1.000000     1.000000

## 欠損値の確認
- 必ずpositivenessが欠損になっている

In [80]:
df_train[df_train.isnull().any(axis=1)]

index  genre  popularity  duration_ms  acousticness  positiveness  danceability   loudness    energy  liveness  speechiness  instrumentalness  tempo    region
169     169     10          29        22132      0.183041           NaN      0.074635  -2.684752  0.424803  0.538192     0.275940          0.874660  57-63  region_L
332     332     10          18         5998      0.073058           NaN           NaN  -3.492185  0.482935       NaN          NaN          0.933298   0-40  region_P
1147   1147     10          17         5999      0.246239           NaN           NaN -11.188019  0.138494       NaN          NaN               NaN   0-40  region_P
1824   1824     10          29        12904      0.878264           NaN           NaN -37.820457  0.071458  0.306170          NaN          0.209245   0-40  region_B
1859   1859     10          17         6002      0.166670           NaN           NaN  -3.675506  0.630632       NaN          NaN          0.878543   0-40  region_P
1894   1894      8          28        12105      0.894437           NaN           NaN -30.401654  0.294521  0.680640          NaN          0.353691   0-40  region_E
1942   1942     10          30        13559      0.125577           NaN           NaN   0.000000  0.856918  0.521328          NaN          0.809948   0-40  region_L
2088   2088     10          30        20748      0.149761           NaN      0.222094  -3.491594  0.814625  0.243798     0.302897          0.866409  64-76  region_L
2290   2290      4          54       256385      0.862298           NaN           NaN -14.370051  0.127264  0.260063          NaN          0.195740   0-40  region_P
2619   2619     10          28        12907      0.174814           NaN           NaN  -4.747260  0.887299  0.493169          NaN          0.810391   0-40  region_L

In [81]:
df_test[df_test.isnull().any(axis=1)]

index  popularity  duration_ms  acousticness  positiveness  danceability   loudness    energy  liveness  speechiness  instrumentalness  tempo    region
65     4111          32         8307      0.705052           NaN           NaN  -5.838485  0.677236  0.330491          NaN          0.450735   0-40  region_L
161    4207          29         5826      0.303558           NaN           NaN  -3.612817  0.770469       NaN          NaN          0.834549   0-40  region_L
200    4246          16         5998           NaN           NaN           NaN  -9.770362       NaN       NaN          NaN               NaN   0-40  region_P
313    4359          32        15150      0.021372           NaN      0.207516  -1.013198  0.906015  0.516378     0.272722          0.833171  77-96  region_L
848    4894          32        28304      0.133870           NaN      0.313016  -4.504644  0.654447  0.147979     0.144175          0.851650  77-96  region_L
935    4981          28         6199      0.800011           NaN           NaN -30.216122  0.147273       NaN          NaN          0.125978   0-40  region_B
1750   5796          28         6506      0.162008           NaN           NaN  -2.325072  0.845391       NaN          NaN          0.876464   0-40   unknown
1790   5836          18        17375      0.093081           NaN      0.280091  -6.356741  0.459276  0.339337     0.140230          0.712319  64-76  region_P
1834   5880          28         9705      0.088208           NaN           NaN  -6.473317  0.919014  0.506552          NaN          0.742145   0-40  region_L
2018   6064          34        13629      0.067932           NaN           NaN  -3.460831  0.921675  0.386363          NaN          0.768600   0-40  region_L
2353   6399          23         6188      0.110493           NaN           NaN  -6.919988  0.657686       NaN          NaN          0.132778   0-40  region_I
2432   6478          31         9589      0.135442           NaN           NaN  -2.267572  0.787650  0.239729          NaN          0.889276   0-40  region_L
3472   7518          30        12118      0.150838           NaN           NaN   0.000000  0.853234  0.543013          NaN          0.733705   0-40  region_L
3605   7651          21         6002      0.247154           NaN           NaN  -8.690648  0.095924       NaN          NaN               NaN   0-40  region_P